In [1]:
!pip install catboost==0.17.5

     |████████████████████████████████| 62.7MB 43.8MB/s 
  Found existing installation: catboost 0.17.3
    Uninstalling catboost-0.17.3:
      Successfully uninstalled catboost-0.17.3


In [2]:
import catboost
catboost.__version__

'0.17.5'

In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from catboost import CatBoostRegressor
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from copy import deepcopy
import matplotlib.pyplot as plt
import seaborn as sns

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

/kaggle/input/tcdml1920-income-ind/tcd ml 2019-20 income prediction submission file example (random solutions).csv
/kaggle/input/tcdml1920-income-ind/tcd ml 2019-20 income prediction submission file.csv
/kaggle/input/tcdml1920-income-ind/tcd ml 2019-20 income prediction test (without labels).csv
/kaggle/input/tcdml1920-income-ind/tcd ml 2019-20 income prediction training (with labels).csv
/kaggle/input/submission/Submission.csv


In [4]:
# Load Training & Test data
data = pd.read_csv('../input/tcdml1920-income-ind/tcd ml 2019-20 income prediction training (with labels).csv', index_col='Instance')
trainData = deepcopy(data.drop(['Income in EUR', 'Hair Color'], axis=1))
data1 = pd.read_csv('../input/tcdml1920-income-ind/tcd ml 2019-20 income prediction test (without labels).csv', index_col='Instance')
testData = deepcopy(data1.drop(['Income', 'Hair Color'], axis=1))

In [5]:
trainData.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 111993 entries, 1 to 111993
Data columns (total 9 columns):
Year of Record       111552 non-null float64
Gender               104561 non-null object
Age                  111499 non-null float64
Country              111993 non-null object
Size of City         111993 non-null int64
Profession           111671 non-null object
University Degree    104623 non-null object
Wears Glasses        111993 non-null int64
Body Height [cm]     111993 non-null int64
dtypes: float64(2), int64(3), object(4)
memory usage: 8.5+ MB


In [6]:
testData.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 73230 entries, 111994 to 185223
Data columns (total 9 columns):
Year of Record       72935 non-null float64
Gender               68368 non-null object
Age                  72951 non-null float64
Country              73230 non-null object
Size of City         73230 non-null int64
Profession           73035 non-null object
University Degree    68373 non-null object
Wears Glasses        73230 non-null int64
Body Height [cm]     73230 non-null int64
dtypes: float64(2), int64(3), object(4)
memory usage: 5.6+ MB


In [7]:
pd.options.display.float_format = '{:.2f}'.format
data['Income in EUR'].describe()

count    111993.00
mean     109213.81
std      149802.35
min       -5696.91
25%       30771.69
50%       57339.17
75%      126093.60
max     5285252.36
Name: Income in EUR, dtype: float64

In [8]:
# Row Duplication check Train & Test
duplicateRowsTrain = trainData[trainData.duplicated()]
print('train' +duplicateRowsTrain)

duplicateRowsTest = testData[testData.duplicated()]
print('test' + duplicateRowsTest)

Empty DataFrame
Columns: [Year of Record, Gender, Age, Country, Size of City, Profession, University Degree, Wears Glasses, Body Height [cm]]
Index: []
Empty DataFrame
Columns: [Year of Record, Gender, Age, Country, Size of City, Profession, University Degree, Wears Glasses, Body Height [cm]]
Index: []


In [9]:
# Null check Train
trainData.isnull().sum().sort_values()

Country                 0
Size of City            0
Wears Glasses           0
Body Height [cm]        0
Profession            322
Year of Record        441
Age                   494
University Degree    7370
Gender               7432
dtype: int64

In [10]:
# Replace train missing values with 'unknown', 'others' and dropping NaN
trainData1 = deepcopy(trainData)
trainData1['Gender']            = trainData1['Gender'].replace({np.nan: 'unknown'})
trainData1['University Degree'] = trainData1['University Degree'].replace({np.nan: 'unknown'})
trainData1['Profession']        = trainData1['Profession'].replace({np.nan: 'others'})
trainData1 = trainData1.dropna()

In [11]:
# Null check Test
testData.isnull().sum().sort_values()

Country                 0
Size of City            0
Wears Glasses           0
Body Height [cm]        0
Profession            195
Age                   279
Year of Record        295
University Degree    4857
Gender               4862
dtype: int64

In [12]:
# Replace test missing values with 'unknown', 'others' and replace NaN with mean
testData1 = deepcopy(testData)
testData1['Gender']            = testData1['Gender'].replace({np.nan: 'unknown'})
testData1['University Degree'] = testData1['University Degree'].replace({np.nan: 'unknown'})
testData1['Profession']        = testData1['Profession'].replace({np.nan: 'others'})
testData1['Year of Record']    = testData1['Year of Record'].replace({np.nan: testData1['Year of Record'].mean()})
testData1['Age']               = testData1['Age'].replace({np.nan: testData1['Age'].mean()})
testData1 = testData1.dropna()

In [13]:
testData1['University Degree'].value_counts()

Bachelor    27914
Master      17890
No          17705
unknown      4857
PhD          4405
0             459
Name: University Degree, dtype: int64

In [14]:
# unknown and zero mapping to downsize categories

trainData1['University Degree'].where(trainData1['University Degree'] == 0, 'unknown')
trainData1['Gender'].where(trainData1['Gender'] == 0, 'unknown')

testData1['University Degree'].where(testData1['University Degree'] == 0, 'unknown')
testData1['Gender'].where(testData1['Gender'] == 0, 'unknown')

Instance
111994    unknown
111995    unknown
111996    unknown
111997    unknown
111998    unknown
           ...   
185219    unknown
185220    unknown
185221    unknown
185222    unknown
185223    unknown
Name: Gender, Length: 73230, dtype: object

In [15]:
trainData1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 111060 entries, 1 to 111993
Data columns (total 9 columns):
Year of Record       111060 non-null float64
Gender               111060 non-null object
Age                  111060 non-null float64
Country              111060 non-null object
Size of City         111060 non-null int64
Profession           111060 non-null object
University Degree    111060 non-null object
Wears Glasses        111060 non-null int64
Body Height [cm]     111060 non-null int64
dtypes: float64(2), int64(3), object(4)
memory usage: 8.5+ MB


In [16]:
testData1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 73230 entries, 111994 to 185223
Data columns (total 9 columns):
Year of Record       73230 non-null float64
Gender               73230 non-null object
Age                  73230 non-null float64
Country              73230 non-null object
Size of City         73230 non-null int64
Profession           73230 non-null object
University Degree    73230 non-null object
Wears Glasses        73230 non-null int64
Body Height [cm]     73230 non-null int64
dtypes: float64(2), int64(3), object(4)
memory usage: 5.6+ MB


In [17]:
normColumn = ['Year of Record', 'Age', 'Size of City', 'Body Height [cm]']
for col in normColumn:
    trainData1[col] = (trainData1[col] - trainData1[col].mean()) / trainData1[col].std()
    testData1[col] = (testData1[col] - testData1[col].mean()) / testData1[col].std()

In [18]:
#Creating a training set for modeling and validation set to check model performance
X = trainData1
y = data.loc[trainData1.index, 'Income in EUR']


X_train, X_validation, y_train, y_validation = train_test_split(X, y, train_size=0.9, random_state=18313172)
categorical_features_indices = np.array([1, 3, 5, 6,7])


model=CatBoostRegressor(
    iterations=20000,
    depth=10,
    learning_rate=0.001,
    loss_function='RMSE',
    task_type='GPU',
    border_count=32,
    verbose=500,
    random_seed=18313172
)
model.fit(X_train, y_train,cat_features=categorical_features_indices,eval_set=(X_validation, y_validation),plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 149595.7260333	test: 150914.1420584	best: 150914.1420584 (0)	total: 45.1ms	remaining: 15m 2s
500:	learn: 110975.2304253	test: 112377.2620384	best: 112377.2620384 (500)	total: 21.5s	remaining: 13m 55s
1000:	learn: 89339.2754408	test: 90639.6342533	best: 90639.6342533 (1000)	total: 43.9s	remaining: 13m 52s
1500:	learn: 77254.4124608	test: 78299.9275946	best: 78299.9275946 (1500)	total: 1m 7s	remaining: 13m 46s
2000:	learn: 70341.2129667	test: 71191.7507614	best: 71191.7507614 (2000)	total: 1m 31s	remaining: 13m 43s
2500:	learn: 66168.7933118	test: 66919.4712290	best: 66919.4712290 (2500)	total: 1m 56s	remaining: 13m 34s
3000:	learn: 63474.5356981	test: 64223.0711685	best: 64223.0711685 (3000)	total: 2m 19s	remaining: 13m 11s
3500:	learn: 61651.9567450	test: 62439.5555315	best: 62439.5555315 (3500)	total: 2m 42s	remaining: 12m 48s
4000:	learn: 60289.2185402	test: 61212.8852321	best: 61212.8852321 (4000)	total: 3m 9s	remaining: 12m 36s
4500:	learn: 59215.0575239	test: 60318.17843

In [19]:
print(model.get_feature_importance(prettified=True))

          Feature Id  Importances
0            Country        30.65
1                Age        18.44
2     Year of Record        16.90
3         Profession        12.47
4  University Degree         7.72
5   Body Height [cm]         6.08
6       Size of City         3.95
7             Gender         3.36
8      Wears Glasses         0.42


In [20]:
submission = pd.DataFrame()
submission['Instance'] = testData1.index
submission['Income'] = model.predict(testData1)
submission.to_csv('Submission.csv', index = False)